In [7]:
from ngsolve import *
from netgen.geom2d import SplineGeometry
from math import pi
#  (0,1)        Gamma_S         (1,1)
#        +----------------------+
#        |     Subdomain 1      |
#Gamma_S |                      | Gamma_S
#        |        Gamma_I       |
#(0,0.5) +----------------------+ (1,0.5)
#        |                      |
#Gamma_D |                      | Gamma_D
#        |   Subdomain 2        |
#        +----------------------+
#  (0,0)      Gamma_D           (1,0)
#
#Define geometry
geo = SplineGeometry()
points     = [ (0, 0), (1, 0),  (1, 0.5), (1, 1), (0, 1), (0, 0.5)]
pnums    = [geo.AppendPoint(*pt) for pt in points]
l1 = geo.Append(["line", 0, 1], leftdomain=2, rightdomain=0, bc="GammaD")
l2 = geo.Append(["line", 1, 2], leftdomain=2, rightdomain=0, bc="GammaD")
l3 = geo.Append(["line", 2, 3], leftdomain=1, rightdomain=0, bc="GammaS")
l4 = geo.Append(["line", 3, 4], leftdomain=1, rightdomain=0, bc="GammaS")
l5 = geo.Append(["line", 4, 5], leftdomain=1, rightdomain=0, bc="GammaS")
l6 = geo.Append(["line", 5, 0], leftdomain=2, rightdomain=0, bc="GammaD")
l7 = geo.Append(["line", 5, 2], leftdomain=1, rightdomain=2, bc="GammaI")

geo.SetMaterial(1, "stokesregion")
geo.SetMaterial(2, "darcyregion")
mesh = Mesh( geo.GenerateMesh(maxh=0.2) )

Draw(mesh)
#parameter
kappa=1
mu=1
alpha=mu*sqrt(kappa)*(1+4*pi**2)/2
#exact p
pexactD = CoefficientFunction(-2/(pi)*cos(pi*x)*exp(y/2))

k = 2
V = VectorL2(mesh,order=k)
Q = L2(mesh,order=k-1)
Vbar = FacetFESpace(mesh, order = k, dirichlet= "GammaS", definedon = mesh.Materials("stokesregion")) 
QbarS = FacetFESpace(mesh, order = k, definedon=mesh.Materials("stokesregion"))
QbarD = FacetFESpace(mesh, order = k, definedon=mesh.Materials("darcyregion"))
R = NumberSpace(mesh)
X = FESpace([V, Vbar, Vbar, Q, QbarS, QbarD, R])

gfu = GridFunction(X)

(u, ubar1, ubar2, p, pbarS, pbarD, lam1)  = X.TrialFunction()
(v, vbar1, vbar2, q, qbarS, qbarD, lam2)  = X.TestFunction()

ubar = CoefficientFunction((ubar1, ubar2))
vbar = CoefficientFunction((vbar1, vbar2))

ubar_tr = CoefficientFunction((ubar1.Trace(), ubar2.Trace()))
vbar_tr = CoefficientFunction((vbar1.Trace(), vbar2.Trace()))


# Penalty parameter
beta = 10*k**2
n = specialcf.normal(mesh.dim)
h = specialcf.mesh_size

#tensor epsilon 
du = grad(u)
dv = grad(v)
eps_u = 0.5*(du+du.trans)
eps_v = 0.5*(dv+dv.trans)

un=ubar_tr*n
vn=vbar_tr*n

#tangent components
ut1=ubar1.Trace()-un*n[0]
ut2=ubar2.Trace()-un*n[1]
tan_ubar = CoefficientFunction((ut1,ut2), dims=(2,1))

vt1=vbar1.Trace()-vn*n[0]
vt2=vbar2.Trace()-vn*n[1]
tan_vbar = CoefficientFunction((vt1,vt2), dims=(2,1))


a = BilinearForm(X)
# Stokes
#ah_S(U,V)
ahS_dx =  2*mu*InnerProduct(eps_u, eps_v)
ahS_ds = (2*beta*mu/h)*InnerProduct(u-ubar, v-vbar) \
          - 2*mu*InnerProduct ( eps_u*n, v-vbar ) \
          - 2*mu*InnerProduct ( eps_v*n, u-ubar)
#bh_S(P,v)+bh_S(Q,u)
bhS_dx = - div(u)*q - div(v)*p
bhS_ds =   pbarS*v*n + qbarS*u*n
# Darcy
#ah_D+bh_D(p,v)+bh_D(q,u)
ahD_dx = (1/kappa)*u*v
bhD_dx = - div(u)*q - div(v)*p
bhD_ds =   pbarD*v*n + qbarD*u*n

# interface Gamma_I
ah_I = alpha*sqrt(1/kappa)*InnerProduct(tan_ubar,tan_vbar)
bh_IS = - pbarS.Trace()*vbar_tr*n - qbarS.Trace()*ubar_tr*n
bh_ID = - pbarD.Trace()*vbar_tr*n - qbarD.Trace()*ubar_tr*n
interface_term = ah_I + bh_IS + bh_ID

a += (ahS_dx +bhS_dx)*dx(definedon=mesh.Materials("stokesregion"))
a += (ahD_dx + bhD_dx)*dx(definedon=mesh.Materials("darcyregion"))
a += (ahS_ds + bhS_ds)*dx(element_boundary = True, definedon=mesh.Materials("stokesregion"))
a += bhD_ds*dx(element_boundary = True, definedon=mesh.Materials("darcyregion"))


#a += interface_term*ds(defined =mesh.Boundaries("GammaI"))
a += SymbolicBFI(interface_term, definedon=mesh.Boundaries("GammaI"))

a += (p*lam2 + q*lam1)*dx

# Linear form
f  = LinearForm(X)
#f += fS*v*dx(definedon=mesh.Materials("stokesregion"))
#f += fD*q*dx(definedon=mesh.Materials("darcyregion"))


#fbc_D =   qbarD.Trace()*uexactD*n
#f += fbc_D*ds(definedon=mesh.Boundaries("GammaD"))

a.Assemble()
f.Assemble()

# boundary condition
#gfu.components[1].Set(uexactS[0], definedon=mesh.Boundaries("GammaS"))
#gfu.components[2].Set(uexactS[1], definedon=mesh.Boundaries("GammaS"))

#Solve
inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")

res = f.vec.CreateVector()
res.data = f.vec - a.mat*gfu.vec
gfu.vec.data += inv * res

#L2-error

p = gfu.components[3]
print ("L2-error of p_D:", sqrt (Integrate ( (p-pexactD)**2, mesh, definedon=mesh.Materials("darcyregion" ))))

#Draw
velocity = gfu.components[0]
Draw(velocity,mesh,"u")
pressure = gfu.components[3]
Draw(pressure,mesh,"p")




L2-error of p_D: 0.3625719426254603
